In [1]:
import numpy as np
import pandas as pd

In [2]:
data_yf = pd.read_csv('data/all_stock_data.csv')

In [3]:
data_yf.head()

Date      Open      High       Low     Close  Adj Close     Volume  \
0  2005-01-01 -0.479414 -0.478115 -0.479494 -0.478268  -0.430459  34.087736   
1  2005-01-08 -0.478904 -0.477645 -0.479421 -0.478172  -0.430378  70.853282   
2  2005-01-15 -0.478902 -0.477922 -0.478959 -0.478143  -0.430353  22.545792   
3  2005-01-22 -0.478788 -0.477689 -0.478668 -0.477792  -0.430053  24.219563   
4  2005-01-29 -0.478424 -0.477107 -0.478257 -0.477302  -0.429635  29.468248   

  Ticker      macd  macd_signal  ...  kc_lag_4  kc_lag_12  vwap_lag_4  \
0   AAPL -0.792297     0.574227  ...  1.448724   1.402185    1.504296   
1   AAPL -2.178328    -0.005610  ...  1.457609   1.401363    1.523928   
2   AAPL -3.239398    -0.695964  ...  1.469719   1.402560    1.537420   
3   AAPL -4.033506    -1.417747  ...  1.484467   1.404472    1.553661   
4   AAPL -4.609292    -2.118075  ...  1.393936   1.412477   -0.010326   

   vwap_lag_12  eom_lag_4  eom_lag_12  vpt_lag_4  vpt_lag_12  gain_loss_pct  \
0     1.421333  -0.182704    0.206849  -5.012456   -5.014641       1.502846   
1     1.415932   0.073169    0.082043  -5.012819   -5.014711       0.061165   
2     1.401800   0.036783    0.209130  -5.012615   -5.014387       0.148618   
3     1.401408   0.037899    0.369099  -5.012571   -5.012814       0.897755   
4     1.417726 -26.789164    0.611727  -6.031577   -5.011644       1.233924   

   win  
0    1  
1    1  
2    1  
3    1  
4    1  

[5 rows x 53 columns]

In [4]:
data_yf.isna().any().any()

False

In [5]:
#create a list of dataframes
symbols = list(data_yf['Ticker'].value_counts().index)

df_list = []

# Loop over each unique ticker
for ticker in range(len(symbols)):
    df = data_yf[data_yf['Ticker'] == symbols[ticker]]
    
    # Rename all columns in df to "original_column_nameTicker"
    df.columns = [str(col) + str(symbols[ticker]) for col in df.columns]
    
    df = df.reset_index().drop(columns=['index'])#[0:990]
    
    # Append modified df to the list
    df_list.append(df)

In [6]:
num_null = 0

for df in df_list:
    if df.isna().any().any() == True:
        num_null +=1 
        
data = pd.concat(df_list, axis=1)


data.set_index('DateFITB', inplace=True)

In [7]:
date_values = [col for col in data.columns if 'Date' in col]
data.drop(columns=date_values, inplace=True)

Now, we will do Predict then Optimize -- Shared Learning

<h2> Predict then Optimize -- Shared Learning</h2>

In [8]:
#keep only float columns for model
float_columns = data.select_dtypes(include=['float64']).columns

data = data[float_columns]

data.dropna(inplace=True)

In [9]:
data.shape

(991, 18658)

In [10]:
data.head()

OpenHUBB  HighHUBB   LowHUBB  CloseHUBB  Adj CloseHUBB  \
DateFITB                                                             
2005-01-01 -0.192880 -0.200248 -0.205898  -0.211361      -0.265456   
2005-01-08 -0.211098 -0.207003 -0.203862  -0.200142      -0.258453   
2005-01-15 -0.199839 -0.205136 -0.198045  -0.204427      -0.261127   
2005-01-22 -0.204705 -0.211726 -0.209970  -0.209839      -0.264505   
2005-01-29 -0.208722 -0.204752 -0.201244  -0.198338      -0.257327   

            VolumeHUBB  macdHUBB  macd_signalHUBB   rsiHUBB  bb_highHUBB  ...  \
DateFITB                                                                  ...   
2005-01-01   -0.211835  0.015382        -0.015572 -0.823862    -0.184796  ...   
2005-01-08   -0.208565 -0.000038        -0.012498 -0.545461    -0.185271  ...   
2005-01-15   -0.211585 -0.015709        -0.013384 -0.633585    -0.186998  ...   
2005-01-22   -0.210209 -0.032342        -0.017643 -0.746704    -0.187483  ...   
2005-01-29   -0.211662 -0.035359        -0.021694 -0.438971    -0.187682  ...   

            kc_lag_4BIO  kc_lag_12BIO  vwap_lag_4BIO  vwap_lag_12BIO  \
DateFITB                                                               
2005-01-01     0.027477      0.068128       0.002741        0.072400   
2005-01-08     0.025023      0.064088       0.011129        0.059041   
2005-01-15     0.024448      0.058865       0.013247        0.043133   
2005-01-22     0.024523      0.054117       0.016038        0.024245   
2005-01-29     0.012706      0.049033       0.015927        0.013507   

            eom_lag_4BIO  eom_lag_12BIO  vpt_lag_4BIO  vpt_lag_12BIO  \
DateFITB                                                               
2005-01-01      0.181153      -0.062487      1.469704       1.469331   
2005-01-08      1.024422       0.009616      1.469906       1.469320   
2005-01-15      0.100286      -0.104939      1.469894       1.469285   
2005-01-22      0.021611       0.179215      1.469896       1.469392   
2005-01-29     -1.679183       0.009561      1.469859       1.469358   

            gain_loss_pctBIO  winBIO  
DateFITB                              
2005-01-01         -0.909825    -1.0  
2005-01-08         -0.106853     0.0  
2005-01-15          0.534066     1.0  
2005-01-22         -0.414430    -1.0  
2005-01-29          0.274351     1.0  

[5 rows x 18658 columns]

In [11]:
data.to_csv('data/all_stock_data_transformed_horizontally.csv')

In [12]:
import tensorflow as tf
from scipy.optimize import minimize

In [ ]:
# Use GPU if available
device_name = "GPU" if tf.config.experimental.list_physical_devices('GPU') else "cpu"
print("Using device:", device_name)

Using device: GPU


In [ ]:
# Check type of GPU available on machine
physical_devices = tf.config.list_physical_devices()
print("Available devices:", physical_devices)

Available devices: [PhysicalDevice(name='/physical_device:CPU:0', device_type='CPU'), PhysicalDevice(name='/physical_device:GPU:0', device_type='GPU')]


In [ ]:
# Prepare features and targets for model training
def prepare_features_targets(data_2):
#     indicators = calculate_technical_indicators(data)
#     returns = np.log(data / data.shift(1)).add_suffix('_returns')
#     full_data = pd.concat([indicators, returns], axis=1).dropna()
    features = data_2[[col for col in data_2.columns if 'gain_loss_' not in col]]
    targets = data_2[[col for col in data_2.columns if 'gain_loss_' in col]]
    return features, targets

# Build and compile a neural network
def build_model(input_shape, output_shape):
    with tf.device(device_name):
        model = tf.keras.Sequential([
            tf.keras.layers.Dense(64, activation='relu', kernel_initializer='he_normal',input_shape=(input_shape,)),
            tf.keras.layers.Dense(32, activation='relu',kernel_initializer='he_normal'),
            tf.keras.layers.Dense(output_shape)
        ])
    model.compile(optimizer='adam', loss='mse')
    return model

# Portfolio optimization function with variance consideration and risk aversion
def optimize_portfolio(weights, model, features, historical_returns, risk_aversion=0.8):
    weights = weights / np.sum(weights)  # Normalize weights
    pred_returns = model.predict(np.array([features.iloc[-1]]))[0]
    expected_return = np.dot(weights, pred_returns)
    covariance_matrix = historical_returns.cov()
    portfolio_variance = np.dot(weights.T, np.dot(covariance_matrix, weights))
    # Objective function with risk aversion parameter
    return -expected_return + risk_aversion * portfolio_variance  # Maximize returns and penalize variance


In [ ]:
#set index to datetime
data.index = pd.to_datetime(data.index)

In [ ]:
# Main script
#features, targets = prepare_features_targets(data)
with tf.device(device_name):
    print(device_name)
    # Your model code here
    split_date = pd.Timestamp('2023-01-01')
    # Prepare your features and targets first
    features, targets = prepare_features_targets(data)
    # Split the data based on the threshold date
    train_features = features[features.index < split_date]
    test_features = features[features.index >= split_date]
    train_targets = targets[targets.index < split_date]
    test_targets = targets[targets.index >= split_date]
    model = build_model(train_features.shape[1], train_targets.shape[1])
    model.fit(train_features, train_targets, epochs=20, batch_size=5)

constraints = {'type': 'eq', 'fun': lambda weights: np.sum(weights) - 1}
initial_weights = np.ones(len(symbols)) / len(symbols) # Equal weights
bounds = tuple((0, 1) for _ in symbols)


with tf.device(device_name):
    # Optimizing the portfolio on training data
    train_optimized_result = minimize(optimize_portfolio, initial_weights, args=(model, train_features, train_targets, 1), bounds=bounds, constraints=constraints)
    optimized_weights_train = train_optimized_result.x

    # Optimizing the portfolio on testing data
    test_optimized_result = minimize(optimize_portfolio, initial_weights, args=(model, test_features, test_targets, 1), bounds=bounds, constraints=constraints)
    optimized_weights_test = test_optimized_result.x

    # Calculating ROI
    train_predicted_returns = model.predict(train_features)
    train_roi = np.dot(optimized_weights_train, train_predicted_returns.mean(axis=0)) * 10000  # Assuming $10,000 initial investment

    test_predicted_returns = model.predict(test_features)
    test_roi = np.dot(optimized_weights_test, test_predicted_returns.mean(axis=0)) * 10000  # Assuming $10,000 initial investment


GPU


2024-05-02 11:57:11.676396: I metal_plugin/src/device/metal_device.cc:1154] Metal device set to: Apple M1 Pro
2024-05-02 11:57:11.676423: I metal_plugin/src/device/metal_device.cc:296] systemMemory: 16.00 GB
2024-05-02 11:57:11.676430: I metal_plugin/src/device/metal_device.cc:313] maxCacheSize: 5.33 GB
2024-05-02 11:57:11.676447: I tensorflow/core/common_runtime/pluggable_device/pluggable_device_factory.cc:305] Could not identify NUMA node of platform GPU ID 0, defaulting to 0. Your kernel may not have been built with NUMA support.
2024-05-02 11:57:11.676459: I tensorflow/core/common_runtime/pluggable_device/pluggable_device_factory.cc:271] Created TensorFlow device (/job:localhost/replica:0/task:0/device:GPU:0 with 0 MB memory) -> physical PluggableDevice (device: 0, name: METAL, pci bus id: <undefined>)
/Users/MV/anaconda3/lib/python3.11/site-packages/keras/src/layers/core/dense.py:87: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential m

Epoch 1/20


2024-05-02 11:57:12.271224: I tensorflow/core/grappler/optimizers/custom_graph_optimizer_registry.cc:117] Plugin optimizer for device_type GPU is enabled.


188/188 ━━━━━━━━━━━━━━━━━━━━ 4s 13ms/step - loss: 1007390145554415616.0000
Epoch 2/20
188/188 ━━━━━━━━━━━━━━━━━━━━ 2s 12ms/step - loss: 0.0023
Epoch 3/20
188/188 ━━━━━━━━━━━━━━━━━━━━ 2s 11ms/step - loss: 0.0020
Epoch 4/20
188/188 ━━━━━━━━━━━━━━━━━━━━ 2s 11ms/step - loss: 0.0020
Epoch 5/20
188/188 ━━━━━━━━━━━━━━━━━━━━ 2s 12ms/step - loss: 0.0021
Epoch 6/20
188/188 ━━━━━━━━━━━━━━━━━━━━ 2s 12ms/step - loss: 0.0022
Epoch 7/20
188/188 ━━━━━━━━━━━━━━━━━━━━ 2s 12ms/step - loss: 0.0021
Epoch 8/20
188/188 ━━━━━━━━━━━━━━━━━━━━ 2s 11ms/step - loss: 0.0020
Epoch 9/20
188/188 ━━━━━━━━━━━━━━━━━━━━ 2s 11ms/step - loss: 0.0021
Epoch 10/20
188/188 ━━━━━━━━━━━━━━━━━━━━ 2s 11ms/step - loss: 0.0021
Epoch 11/20
188/188 ━━━━━━━━━━━━━━━━━━━━ 2s 11ms/step - loss: 0.0021
Epoch 12/20
188/188 ━━━━━━━━━━━━━━━━━━━━ 2s 11ms/step - loss: 0.0021
Epoch 13/20
188/188 ━━━━━━━━━━━━━━━━━━━━ 2s 13ms/step - loss: 0.0020
Epoch 14/20
188/188 ━━━━━━━━━━━━━━━━━━━━ 2s 12ms/step - loss: 0.0020
Epoch 15/20
188/188 ━━━━━━━━━━━━━━━━

In [ ]:
print("Optimized Portfolio Weights (Train):", optimized_weights_train)
print("Training ROI:", train_roi)
print("Optimized Portfolio Weights (Test):", optimized_weights_test)
print("Testing ROI:", test_roi)

Optimized Portfolio Weights (Train): [5.80493075e-17 0.00000000e+00 0.00000000e+00 1.50002274e-01
 1.51318782e-16 0.00000000e+00 0.00000000e+00 2.13191552e-18
 0.00000000e+00 8.65584607e-02 0.00000000e+00 0.00000000e+00
 9.58262376e-19 0.00000000e+00 0.00000000e+00 0.00000000e+00
 0.00000000e+00 6.08763744e-18 6.49731078e-17 0.00000000e+00
 2.73972421e-17 4.20887185e-17 2.53445476e-17 0.00000000e+00
 1.31540780e-18 0.00000000e+00 5.29828771e-17 0.00000000e+00
 0.00000000e+00 3.36215610e-18 1.71787761e-17 0.00000000e+00
 0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
 0.00000000e+00 2.86560638e-17 0.00000000e+00 3.58056963e-17
 3.79155090e-17 1.89357592e-17 0.00000000e+00 0.00000000e+00
 8.21262823e-18 0.00000000e+00 0.00000000e+00 3.22108608e-17
 0.00000000e+00 0.00000000e+00 1.17958759e-16 0.00000000e+00
 0.00000000e+00 0.00000000e+00 7.20645099e-17 4.13510117e-17
 1.10565925e-16 0.00000000e+00 3.74799512e-01 4.01838426e-17
 6.95431137e-17 0.00000000e+00 6.37118213e-17 0.

In [ ]:
tickers = [col.split('_')[0] for col in targets.columns]


def print_non_zero_weights(weights, title, tickers):
    # Using a threshold to consider weights effectively zero
    threshold = 1e-10
    non_zero_weights = {tickers[index]: weight for index, weight in enumerate(weights) if weight > threshold}
    print(f"{title} (non-zero weights):")
    for ticker, weight in non_zero_weights.items():
        print(f"{ticker}: Weight {weight}")

# Assuming 'symbols' is a list of ticker symbols corresponding to the indices of the weights! 
# Need to confirm this... otherwise the assumed tickers below will be wrong
print_non_zero_weights(optimized_weights_train, "Optimized Portfolio Weights (Train)", symbols)
print("Training ROI:", train_roi)
print_non_zero_weights(optimized_weights_test, "Optimized Portfolio Weights (Test)", symbols)
print("Testing ROI:", test_roi)



Optimized Portfolio Weights (Train) (non-zero weights):
PPL: Weight 0.15000227401795924
NTAP: Weight 0.08655846069264007
TSCO: Weight 0.3747995122931056
DGX: Weight 0.1749298384317444
AZO: Weight 0.21370991456455518
Training ROI: 144.55907131516034
Optimized Portfolio Weights (Test) (non-zero weights):
TSCO: Weight 0.9240065937193032
AZO: Weight 0.0759934062806995
Testing ROI: 152.5923516725136


In [ ]:
# import numpy as np
# import pandas as pd
# import tensorflow as tf
# from scipy.optimize import minimize
# from sklearn.model_selection import train_test_split
# from sklearn.metrics import mean_squared_error

# # Prepare features and targets for model training
# def prepare_features_targets(data):
#     features = data[[col for col in data.columns if 'gain' not in col]]
#     targets = data[[col for col in data.columns if 'gain' in col]]
#     return features, targets

# # Build and compile a neural network
# def build_model(input_shape, output_shape):
#     model = tf.keras.Sequential([
#         tf.keras.layers.Dense(64, activation='relu', input_shape=(input_shape,)),
#         tf.keras.layers.Dense(32, activation='relu'),
#         tf.keras.layers.Dense(output_shape)
#     ])
#     model.compile(optimizer='adam', loss='mse')
#     return model

# # Portfolio optimization function with variance consideration and risk aversion
# def optimize_portfolio(weights, model, features, historical_returns, risk_aversion=0.8):
#     weights = weights / np.sum(weights)  # Normalize weights
#     pred_returns = model.predict(features)[-1]  # Predicting the last set of features
#     expected_return = np.dot(weights, pred_returns)
#     covariance_matrix = historical_returns.cov()
#     portfolio_variance = np.dot(weights.T, np.dot(covariance_matrix, weights))
#     return -expected_return + risk_aversion * portfolio_variance  # Maximize returns and penalize variance

# column_values = [col for col in data.columns if 'EXC' or 'APPL' in col]
# data_2 = data[column_values]

# symbols = ['EXC', 'AAPL']

# # Prepare features and targets
# features, targets = prepare_features_targets(data_2)

# # Split data into training and testing sets
# train_features, test_features, train_targets, test_targets = train_test_split(features, targets, test_size=0.2, random_state=42)

# # Build model
# model = build_model(train_features.shape[1], train_targets.shape[1])

# # Train model
# model.fit(train_features, train_targets, epochs=3, batch_size=32)

# # Optimizing portfolio using training data
# # train_returns = train_features.pct_change().dropna()
# initial_weights = np.ones(len(symbols)) / len(symbols)
# bounds = tuple((0, 1) for _ in symbols)
# constraints = {'type': 'eq', 'fun': lambda weights: np.sum(weights) - 1}

# optimized_result_train = minimize(optimize_portfolio, initial_weights, args=(model, train_features, train_targets, 0.8), bounds=bounds, constraints=constraints)
# optimized_weights_train = optimized_result_train.x

# # Calculate ROI for the training set
# train_predicted_returns = model.predict(train_features)
# train_roi = np.dot(optimized_weights_train, train_predicted_returns.mean(axis=0)) * 10000  # Assuming $10,000 initial investment

# # Optimizing portfolio using testing data
# test_returns = test_features.pct_change().dropna()
# optimized_result_test = minimize(optimize_portfolio, initial_weights, args=(model, test_features, test_targets, 0.8), bounds=bounds, constraints=constraints)
# optimized_weights_test = optimized_result_test.x

# # Calculate ROI for the testing set
# test_predicted_returns = model.predict(test_features)
# test_roi = np.dot(optimized_weights_test, test_predicted_returns.mean(axis=0)) * 10000  # Assuming $10,000 initial investment

# print(f"Training ROI: ${train_roi:.2f}")
# print(f"Testing ROI: ${test_roi:.2f}")
# print("Optimized Weights for Training Set:", optimized_weights_train)
# print("Optimized Weights for Testing Set:", optimized_weights_test)


Non Shared Learning


In [ ]:
data_yf

Date        Open        High         Low       Close  \
0       2005-01-01    1.156786    1.243393    1.117857    1.236607   
1       2005-01-08    1.246964    1.328929    1.130357    1.253571   
2       2005-01-15    1.247321    1.278571    1.209821    1.258750   
3       2005-01-22    1.267500    1.321071    1.259821    1.321071   
4       2005-01-29    1.331786    1.426964    1.330536    1.407857   
...            ...         ...         ...         ...         ...   
393423  2023-11-25  308.980011  309.140015  300.309998  307.000000   
393424  2023-12-02  305.029999  314.730011  302.649994  304.130005   
393425  2023-12-09  305.160004  324.359985  293.019989  306.119995   
393426  2023-12-16  309.480011  324.619995  305.670013  320.739990   
393427  2023-12-23  321.000000  326.600006  317.209991  322.890015   

         Adj Close        Volume Ticker       macd  macd_signal  ...  \
0         1.046911  5.402242e+09   AAPL -13.373668     9.077173  ...   
1         1.061272  1.119210e+10   AAPL -36.761577    -0.090577  ...   
2         1.065657  3.584610e+09   AAPL -54.666090   -11.005680  ...   
3         1.118418  3.848197e+09   AAPL -68.065895   -22.417723  ...   
4         1.191891  4.674762e+09   AAPL -77.781714   -33.490521  ...   
...            ...           ...    ...        ...          ...  ...   
393423  307.000000  1.314000e+06    BIO -29.253501   -26.633778  ...   
393424  304.130005  1.346600e+06    BIO -28.537459   -27.014514  ...   
393425  306.119995  2.165200e+06    BIO -27.492499   -27.110111  ...   
393426  320.739990  1.558000e+06    BIO -25.194226   -26.726934  ...   
393427  322.890015  4.725000e+05    BIO -22.934959   -25.968539  ...   

          kc_lag_4   kc_lag_12  vwap_lag_4  vwap_lag_12     eom_lag_4  \
0       339.237835  331.084166  345.780999   331.409048 -2.818720e+07   
1       340.791002  330.940500  349.180141   330.474001  8.035444e+06   
2       342.908001  331.149667  351.516383   328.027238  2.884406e+06   
3       345.486002  331.484000  354.328406   327.959388  3.042372e+06   
4       329.660633  332.883168   83.529489   330.784544 -3.794730e+09   
...            ...         ...         ...          ...           ...   
393423  367.556667  388.930166  348.202551   388.240907 -1.106816e+08   
393424  364.304833  385.117499  334.948759   388.640884  1.759941e+08   
393425  360.818000  382.635166  327.026048   388.540736  4.647516e+07   
393426  357.157833  381.777833  324.021093   388.852380 -2.339939e+06   
393427  352.671500  380.411499  320.852712   388.247468 -2.545445e+06   

          eom_lag_12     vpt_lag_4    vpt_lag_12  gain_loss_pct  win  
0       2.698811e+07  2.394464e+08  2.223275e+08       0.069002    1  
1       9.307251e+06  2.375267e+08  2.219597e+08       0.005299    1  
2       2.731130e+07  2.386018e+08  2.236732e+08       0.009163    1  
3       4.997345e+07  2.388381e+08  2.319839e+08       0.042265    1  
4       8.434586e+07 -5.145638e+09  2.381677e+08       0.057119    1  
...              ...           ...           ...            ...  ...  
393423 -2.701442e+08  3.449437e+10  3.449469e+10      -0.006408   -1  
393424 -1.750192e+07  3.449450e+10  3.449475e+10      -0.002951   -1  
393425 -3.950084e+07  3.449447e+10  3.449471e+10       0.003146    0  
393426 -3.299103e+07  3.449450e+10  3.449472e+10       0.036384    1  
393427 -8.896700e+06  3.449448e+10  3.449472e+10       0.005888    1  

[393428 rows x 53 columns]

In [ ]:
#Need a train loader and a test loader
#Need to convert to optDataset, then wrap with DataLoader

In [ ]:
!pip install PyPl gurobipy pyepo

Create a LSTM-based model for stock prediction tasks

In [ ]:
import torch.nn.functional as F
from torch import nn
import torch 
class StockLSTM(nn.Module):

    def __init__(self, vocab_size, embedding_dim, hidden_dim, num_layers=1):
        super(StockLSTM, self).__init__()
        self.embedding = nn.Embedding(vocab_size, embedding_dim)
        self.lstm = nn.LSTM(embedding_dim, hidden_dim,num_layers=num_layers, batch_first=True)
        self.fc = nn.Linear(hidden_dim, vocab_size)

    def forward(self, x):
        x = self.embedding(x)
        all_h, (h, c) = self.lstm(x)
        out = self.fc(all_h) # Apply Linear layer to outputs from all the hidden state.
        return out

In [ ]:
import gurobipy as gp
from gurobipy import GRB
import numpy as np
import pyepo
from pyepo.model.grb import optGrbModel
import torch
from torch import nn
from torch.utils.data import DataLoader

m = 50 # change based on number of assets
cov = np.cov(np.random.randn(10, m), rowvar=False) # covariance matrix
optmodel = pyepo.model.grb.portfolioModel(m, cov) # build model

Auto-Sklearn cannot be imported.
Restricted license - for non-production use only - expires 2025-11-24


In [ ]:
import time

# train model
def trainModel(reg, loss_func, method_name, num_epochs=20, lr=1e-2):
    # set adam optimizer
    optimizer = torch.optim.Adam(reg.parameters(), lr=lr)
    # train mode
    reg.train()
    # init log
    train_loss_log = []
    loss_log_regret = [pyepo.metric.regret(reg, optmodel, loader_test)]
    # init elpased time
    elapsed = 0
    for epoch in range(num_epochs):
        # start timing
        tick = time.time()
        # load data
        train_loss = 0
        for i, data in enumerate(loader_train):
            x, c, w, z = data
            # cuda
            if torch.cuda.is_available():
                x, c, w, z = x.cuda(), c.cuda(), w.cuda(), z.cuda()
            # forward pass
            cp = reg(x)
            if method_name == "spo+":
                loss = loss_func(cp, c, w, z)
            elif method_name == "mse":
                loss = loss_func(cp, c)
            else:
                raise ValueError("Method name {} not supported".format(method_name))
            # backward pass
            optimizer.zero_grad()
            loss.backward()
            optimizer.step()
            # record time
            tock = time.time()
            elapsed += tock - tick
            train_loss += loss.item()
        train_loss /= len(loader_train)
        train_loss_log.append(train_loss)
        regret = pyepo.metric.regret(reg, optmodel, loader_test)
        loss_log_regret.append(regret)
        print("Epoch {:2},  Loss: {:9.4f},  Regret: {:7.4f}%".format(epoch+1, train_loss, regret*100))
    print("Total Elapsed Time: {:.2f} Sec.".format(elapsed))
    return train_loss_log, loss_log_regret

Create a Predict-then-Optimize Model

In [ ]:

spop = pyepo.func.SPOPlus(optmodel, processes=1)

In [ ]:
# Hyperparameters
VOCAB_SIZE = #fill in once data is imported
EMBEDDING_DIM = #param we can optimize
HIDDEN_DIM = #also a param to optimize
learning_rate = #another optimizable param
epoch = #optimize
num_layers = #optimize
epochs = 20
learning_rate = 2e-3
method_name = "spo+"

# Instantiate the model
lstm = StockLSTM(VOCAB_SIZE, EMBEDDING_DIM, HIDDEN_DIM,num_layers=num_layers)
loss_log_lstm_spo, loss_log_regret_lstm_spo = trainModel(lstm, loss_func=spop, method_name=method_name)
